In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.linear_model import LinearRegression
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score

df = pd.read_csv('/kaggle/input/mobile/user_behavior_dataset.csv')
df

User ID        Device Model Operating System  App Usage Time (min/day)  \
0          1      Google Pixel 5          Android                       393   
1          2           OnePlus 9          Android                       268   
2          3        Xiaomi Mi 11          Android                       154   
3          4      Google Pixel 5          Android                       239   
4          5           iPhone 12              iOS                       187   
..       ...                 ...              ...                       ...   
695      696           iPhone 12              iOS                        92   
696      697        Xiaomi Mi 11          Android                       316   
697      698      Google Pixel 5          Android                        99   
698      699  Samsung Galaxy S21          Android                        62   
699      700           OnePlus 9          Android                       212   

     Screen On Time (hours/day)  Battery Drain (mAh/day)  \
0                           6.4                     1872   
1                           4.7                     1331   
2                           4.0                      761   
3                           4.8                     1676   
4                           4.3                     1367   
..                          ...                      ...   
695                         3.9                     1082   
696                         6.8                     1965   
697                         3.1                      942   
698                         1.7                      431   
699                         5.4                     1306   

     Number of Apps Installed  Data Usage (MB/day)  Age  Gender  \
0                          67                 1122   40    Male   
1                          42                  944   47  Female   
2                          32                  322   42    Male   
3                          56                  871   20    Male   
4                          58                  988   31  Female   
..                        ...                  ...  ...     ...   
695                        26                  381   22    Male   
696                        68                 1201   59    Male   
697                        22                  457   50  Female   
698                        13                  224   44    Male   
699                        49                  828   23  Female   

     User Behavior Class  
0                      4  
1                      3  
2                      2  
3                      3  
4                      3  
..                   ...  
695                    2  
696                    4  
697                    2  
698                    1  
699                    3  

[700 rows x 11 columns]

In [2]:
df.head(10)

User ID        Device Model Operating System  App Usage Time (min/day)  \
0        1      Google Pixel 5          Android                       393   
1        2           OnePlus 9          Android                       268   
2        3        Xiaomi Mi 11          Android                       154   
3        4      Google Pixel 5          Android                       239   
4        5           iPhone 12              iOS                       187   
5        6      Google Pixel 5          Android                        99   
6        7  Samsung Galaxy S21          Android                       350   
7        8           OnePlus 9          Android                       543   
8        9  Samsung Galaxy S21          Android                       340   
9       10           iPhone 12              iOS                       424   

   Screen On Time (hours/day)  Battery Drain (mAh/day)  \
0                         6.4                     1872   
1                         4.7                     1331   
2                         4.0                      761   
3                         4.8                     1676   
4                         4.3                     1367   
5                         2.0                      940   
6                         7.3                     1802   
7                        11.4                     2956   
8                         7.7                     2138   
9                         6.6                     1957   

   Number of Apps Installed  Data Usage (MB/day)  Age  Gender  \
0                        67                 1122   40    Male   
1                        42                  944   47  Female   
2                        32                  322   42    Male   
3                        56                  871   20    Male   
4                        58                  988   31  Female   
5                        35                  564   31    Male   
6                        66                 1054   21  Female   
7                        82                 1702   31    Male   
8                        75                 1053   42  Female   
9                        75                 1301   42    Male   

   User Behavior Class  
0                    4  
1                    3  
2                    2  
3                    3  
4                    3  
5                    2  
6                    4  
7                    5  
8                    4  
9                    4

In [3]:
gender_mapping = {'Male': 1, 'Female': 0}
df['Gender'] = df['Gender'].map(gender_mapping)

In [4]:
df.dropna(inplace=True)

In [5]:
df.isnull().sum()

User ID                       0
Device Model                  0
Operating System              0
App Usage Time (min/day)      0
Screen On Time (hours/day)    0
Battery Drain (mAh/day)       0
Number of Apps Installed      0
Data Usage (MB/day)           0
Age                           0
Gender                        0
User Behavior Class           0
dtype: int64

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 700 entries, 0 to 699
Data columns (total 11 columns):
 #   Column                      Non-Null Count  Dtype  
---  ------                      --------------  -----  
 0   User ID                     700 non-null    int64  
 1   Device Model                700 non-null    object 
 2   Operating System            700 non-null    object 
 3   App Usage Time (min/day)    700 non-null    int64  
 4   Screen On Time (hours/day)  700 non-null    float64
 5   Battery Drain (mAh/day)     700 non-null    int64  
 6   Number of Apps Installed    700 non-null    int64  
 7   Data Usage (MB/day)         700 non-null    int64  
 8   Age                         700 non-null    int64  
 9   Gender                      700 non-null    int64  
 10  User Behavior Class         700 non-null    int64  
dtypes: float64(1), int64(8), object(2)
memory usage: 60.3+ KB


In [7]:
df.describe()

User ID  App Usage Time (min/day)  Screen On Time (hours/day)  \
count  700.00000                700.000000                  700.000000   
mean   350.50000                271.128571                    5.272714   
std    202.21688                177.199484                    3.068584   
min      1.00000                 30.000000                    1.000000   
25%    175.75000                113.250000                    2.500000   
50%    350.50000                227.500000                    4.900000   
75%    525.25000                434.250000                    7.400000   
max    700.00000                598.000000                   12.000000   

       Battery Drain (mAh/day)  Number of Apps Installed  Data Usage (MB/day)  \
count               700.000000                700.000000           700.000000   
mean               1525.158571                 50.681429           929.742857   
std                 819.136414                 26.943324           640.451729   
min                 302.000000                 10.000000           102.000000   
25%                 722.250000                 26.000000           373.000000   
50%                1502.500000                 49.000000           823.500000   
75%                2229.500000                 74.000000          1341.000000   
max                2993.000000                 99.000000          2497.000000   

              Age      Gender  User Behavior Class  
count  700.000000  700.000000           700.000000  
mean    38.482857    0.520000             2.990000  
std     12.012916    0.499957             1.401476  
min     18.000000    0.000000             1.000000  
25%     28.000000    0.000000             2.000000  
50%     38.000000    1.000000             3.000000  
75%     49.000000    1.000000             4.000000  
max     59.000000    1.000000             5.000000

In [8]:
!pip install numba==0.53.1
!pip install ydata-profiling
!pip install visions --upgrade
!pip install ydata-profiling --upgrade



ERROR: Ignored the following versions that require a different python version: 0.52.0 Requires-Python >=3.6,<3.9; 0.52.0rc3 Requires-Python >=3.6,<3.9; 0.53.0 Requires-Python >=3.6,<3.10; 0.53.0rc1.post1 Requires-Python >=3.6,<3.10; 0.53.0rc2 Requires-Python >=3.6,<3.10; 0.53.0rc3 Requires-Python >=3.6,<3.10; 0.53.1 Requires-Python >=3.6,<3.10; 0.54.0 Requires-Python >=3.7,<3.10; 0.54.0rc2 Requires-Python >=3.7,<3.10; 0.54.0rc3 Requires-Python >=3.7,<3.10; 0.54.1 Requires-Python >=3.7,<3.10
ERROR: Could not find a version that satisfies the requirement numba==0.53.1 (from versions: 0.1, 0.2, 0.3, 0.5.0, 0.6.0, 0.7.0, 0.7.1, 0.7.2, 0.8.0, 0.8.1, 0.9.0, 0.10.0, 0.10.1, 0.11.0, 0.12.0, 0.12.1, 0.12.2, 0.13.0, 0.13.2, 0.13.3, 0.13.4, 0.14.0, 0.15.1, 0.16.0, 0.17.0, 0.18.1, 0.18.2, 0.19.1, 0.19.2, 0.20.0, 0.21.0, 0.22.0, 0.22.1, 0.23.0, 0.23.1, 0.24.0, 0.25.0, 0.26.0, 0.27.0, 0.28.1, 0.29.0, 0.30.0, 0.30.1, 0.31.0, 0.32.0, 0.33.0, 0.34.0, 0.35.0, 0.36.1, 0.36.2, 0.37.0, 0.38.0, 0.38.1, 0.39

In [9]:
from ydata_profiling import ProfileReport

profile = ProfileReport(df)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [10]:
X = df[df.columns[3:10]]
X

App Usage Time (min/day)  Screen On Time (hours/day)  \
0                         393                         6.4   
1                         268                         4.7   
2                         154                         4.0   
3                         239                         4.8   
4                         187                         4.3   
..                        ...                         ...   
695                        92                         3.9   
696                       316                         6.8   
697                        99                         3.1   
698                        62                         1.7   
699                       212                         5.4   

     Battery Drain (mAh/day)  Number of Apps Installed  Data Usage (MB/day)  \
0                       1872                        67                 1122   
1                       1331                        42                  944   
2                        761                        32                  322   
3                       1676                        56                  871   
4                       1367                        58                  988   
..                       ...                       ...                  ...   
695                     1082                        26                  381   
696                     1965                        68                 1201   
697                      942                        22                  457   
698                      431                        13                  224   
699                     1306                        49                  828   

     Age  Gender  
0     40       1  
1     47       0  
2     42       1  
3     20       1  
4     31       0  
..   ...     ...  
695   22       1  
696   59       1  
697   50       0  
698   44       1  
699   23       0  

[700 rows x 7 columns]

In [11]:
y=df["User Behavior Class"]
y

0      4
1      3
2      2
3      3
4      3
      ..
695    2
696    4
697    2
698    1
699    3
Name: User Behavior Class, Length: 700, dtype: int64

In [12]:
X_train,x_test,y_train,y_test = train_test_split(X,y,test_size=0.2,random_state=42)


In [13]:
y_test

158    4
500    1
396    1
155    2
321    3
      ..
24     3
218    5
431    2
281    1
110    2
Name: User Behavior Class, Length: 140, dtype: int64

In [14]:
y_train

82     4
51     3
220    4
669    2
545    1
      ..
71     5
106    2
270    4
435    2
102    2
Name: User Behavior Class, Length: 560, dtype: int64

In [15]:
model = LinearRegression()

In [16]:
model.fit(X_train, y_train)

LinearRegression()

In [17]:
predictions = model.predict(x_test)
predictions

array([4.10905721, 1.10484311, 1.17177727, 2.07641344, 3.11048544,
       1.99679277, 1.76785313, 1.04710448, 3.84365708, 2.83649801,
       1.2150687 , 1.17402313, 1.98212443, 1.20470709, 2.58812757,
       3.97998504, 4.87291689, 1.0474455 , 2.76384026, 1.94360197,
       4.9567729 , 3.8538781 , 2.58465061, 4.00603054, 3.78470513,
       2.05035433, 3.18943374, 4.90931067, 1.86032135, 4.90765325,
       1.13878462, 2.87464268, 1.16969472, 2.85080571, 3.95489774,
       5.03253172, 5.09616312, 1.28791629, 1.31514054, 2.16866153,
       2.90817514, 4.01175663, 1.13116908, 3.09645276, 2.08343671,
       5.04274151, 2.95376954, 2.79251431, 1.21750226, 3.04831353,
       2.1780872 , 2.01869664, 1.6953478 , 1.21493857, 5.23928932,
       4.90627742, 3.01657705, 1.14726148, 3.77620984, 2.13559073,
       3.0831657 , 1.95716139, 1.21416327, 1.80667946, 5.06132502,
       2.17411819, 5.00988093, 1.16578392, 5.08083856, 5.11941736,
       1.10210727, 1.94777882, 2.75129687, 1.84610841, 2.90889

In [18]:
r2 = r2_score(y_test, predictions)
r2

0.982747673912195